# 4. Realspace WFs of graphene

```@meta
CurrentModule = Wannier
```

In this tutorial, we will disentangle the 2D graphene, and compute its realspace representation.

1. construct a `Model` for `Wannier.jl`, by reading the `win`, `amn`, `mmn`, and `eig` files
2. run `Wannier.jl` `disentangle` on the `Model` to minimize the spread
3. write the real space WFs to `xsf` files

!!! note

    Different from previous tutorials, the `amn/mmn/eig/unk` files in this tutorial
    are generated by the [`DFTK.jl`](https://github.com/JuliaMolSim/DFTK.jl/) package.
    See `dftk.jl` script in the tutorial folder for more information.

!!! tip

    This is a HTML version of the tutorial, you can download corresponding
    - Jupyter notebook: [`tutorial.ipynb`](./tutorial.ipynb)
    - Julia script: [`tutorial.jl`](./tutorial.jl)

## Preparation
Load the package

In [ ]:
using Wannier

## Model generation

We will use the `read_w90` function to read the
`win`, `amn`, `mmn`, and `eig` files, and construct a `Model` that abstracts the calculation

In [ ]:
model = read_w90("graphene")

## Disentanglement and maximal localization

The `disentangle` function
will disentangle and maximally localize the spread
functional, and returns the gauge matrices `U`,

In [ ]:
U = disentangle(model);

The initial spread is

In [ ]:
omega(model)

The final spread is

In [ ]:
omega(model, U)

!!! note

    The convergence thresholds is determined by the
    keyword arguments of `disentangle`, e.g., `f_tol` for the tolerance on spread,
    and `g_tol` for the tolerance on the norm of spread gradient, etc. You can use stricter thresholds
    to further minimize a bit the spread.

## Write real space WFs

Now save the `U` to the `model`,

In [ ]:
model.U .= U;

!!! tip

    You need to use `.=` to assign the `U` to the `model`,
    because in Julia `model` is an immutable `struct` so you cannot
    use `model.U = U`.

The `write_realspace_wf` function reads the `UNK` files,
compute the real space WFs in a `n_supercells`-sized super cell,
and write them to `xsf` files,

In [ ]:
write_realspace_wf("wjl", model; n_supercells=3, format=:xsf)

Now, open the `wjl_00001.xsf`, etc. files with a 3D
visualizer, e.g., `vesta`, to have a look at the WFs!

!!! note

    To save space, we use a very coarse kpoint grid and
    reduced sampling of the real space grid, thus the resolution
    are bad, rerun the calculation with a finer kpoint grid and
    see the beautiful WFs 😎

In [ ]:
using JSServe  # hide
Page(; exportable=true, offline=true)  # hide

We also provide a simple plotting package
[`WannierPlots.jl`](https://github.com/qiaojunfeng/WannierPlots.jl)
for quick Visualization of band structure, real space WFs, etc.

First, load the plotting packages

In [ ]:
using WGLMakie
set_theme!(; resolution=(800, 800))
using WannierPlots

!!! tip

    Here we want to show the WFs in this web page, so we first load `WGLMakie`.
    When you use the `WannierPlots` package in REPL, you can first load `GLMakie`,
    then the WFs will be shown in a standalone window.
Read the 1st WF

In [ ]:
xsf = read_xsf("wjl_00001.xsf");

Visualize with `WannierPlots.jl`,

In [ ]:
pos = inv(xsf.primvec) * xsf.atom_positions  # to fractional coordinates
atom_numbers = parse.(Int, xsf.atoms)  # to integer atomic numbers
plot_wf(xsf.rgrid, xsf.W, xsf.primvec, pos, atom_numbers)

## Compute WF centers in realspace

There are some other functions that might be useful for evaluating operators
in real space, e.g., computing WF centers.

First we need to read the `UNK` files, and construct the real space WFs
in a `3 * 3 * 1`-sized super cell (i.e., `model.kgrid`),

In [ ]:
rgrid, W = read_realspace_wf(model, model.kgrid)

The real space WFs `W`, are defined on the grid `rgrid`.

To compute WF centers, invoke

In [ ]:
center(rgrid, W)

columns are the WF centers in Cartesian coordinates.

Compare with WF center computed in reciprocal space,

In [ ]:
center(model)

and yes, they are different, the z coordinate is wrongly computed
in the real space because the WFs are truncated along z (you can
see this by a 3D visualizer). If we translate the `rgrid` by
half of the `c` axis along z, then the WFs are complete, and the
real space WF centers are much closer to the reciprocal space results.

!!! note

    Because we are using a coarsely sampled real space grid in
    the `UNK` files, the WF centers can be improved by
    rerun the calculation with a more refined real space grid.

That's all about real space!

---

*This notebook was generated using [Literate.jl](https://github.com/fredrikekre/Literate.jl).*